In [1]:
import numpy as np
import h5py,glob,os
from pycbc import conversions
from pycbc import coordinates

In [2]:
path = ['/work/yifan.wang/4ogc/release_prod/sumit/',
        '/work/yifan.wang/4ogc/release_prod/shichao_extract/',
        '/work/yifan.wang/4ogc/release_prod/yifan/',
        '/work/yifan.wang/4ogc/release_prod/shilpa/']
posfile = []
for p in path:
    f = glob.glob(p+'/*.hdf')
    posfile.extend(f)
    
configfile =glob.glob('/work/yifan.wang/4ogc/release_prod/allconfig/*_config/*.ini')
#configfile.remove( '/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw200115_042309_clean_highspin.ini')

In [3]:
def custom_sort(name):
    return name.split('GW')[1][:13]
#the 0th is dot, 1st is person name, 2nd is GW event name
posfile.sort(key=custom_sort)

labels = []
for i,path in enumerate(posfile):
    labels.append('GW'+path.split('GW')[1][:13])

In [6]:
def config_sort(name):
    return os.path.basename(name)[12:25]
configfile.sort(key=config_sort)

configfile.remove('/work/yifan.wang/4ogc/release_prod/allconfig/shichao_config/inference-GW190725_174728.ini')

In [9]:
len(configfile),len(posfile)

(94, 94)

In [13]:
for ii,gwname in enumerate(labels):
    with open('./1212_sh_sub/convertsnr_'+gwname+'.sh', 'w') as t:
        t.write('/work/yifan.wang/4ogc/release_prod/yifan/convert_snr/pycbc_inference_model_stats ' +
                '--input-file '+str(posfile[ii]) + ' ' +
                '--output-file /work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/'+gwname+'-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf ' + 
                '--config-file '+str(configfile[ii]) +' --nprocesses 128 --verbose')
        t.close()

In [14]:
for ii,gwname in enumerate(labels):
    with open('./1212_sh_sub/sub_'+gwname+'.sub', 'w') as t:
        t.write('universe = vanilla\n'+
                'accounting_group = cbc.imp.pe\n'+
                'getenv = True\n'+
                'executable = /work/yifan.wang/4ogc/release_prod/convertsnr/1212_sh_sub/convertsnr_'+gwname+'.sh\n'+
                'output = output.'+gwname+'\n'+
                'error = error.'+gwname+'\n'+
                'log = log.'+gwname+'\n'+
                'request_cpus = 128\n'+
                'request_memory = 16000\n'+
                'queue')
        t.close()